In [1]:
import numpy as np
import sys, os
sys.path.append('../../shared/utilsGRF/')
from IPython.display import display
import networkx as nx
import subprocess, glob, re
import matplotlib.pyplot as plt
import sympy
from sympy.parsing.sympy_parser import parse_expr

In [2]:
edges=[]
nnodes_cycle=5
replace_dict=dict()
replace_dict_equal=dict()
c,epsilon,kb,ku=sympy.symbols("c,epsilon,kb,ku")
for i in range(1,nnodes_cycle+1):
    if i%nnodes_cycle!=0:
        i2=i+1
        #print(i)
    else:
        i2=i-nnodes_cycle+1
    edges.append([i,"a%d"%i,i2])
    i_=i+nnodes_cycle
    i2_=i2+nnodes_cycle
    edges.append([i_,"alpha%d"%i,i2_])
    edges.append([i,"kb%d-x"%i,i_])
    edges.append([i_,"ku%d"%i,i])
    exec("epsilon%d=sympy.symbols(\"epsilon%d\")"%(i,i))
    exec("c%d=sympy.symbols(\"c%d\")"%(i,i))
    exec("kb%d=sympy.symbols(\"kb%d\")"%(i,i))
    exec("ku%d=sympy.symbols(\"ku%d\")"%(i,i))
    exec("a%d=sympy.symbols(\"a%d\")"%(i,i))
    exec("alpha%d=sympy.symbols(\"alpha%d\")"%(i,i))
    exec("replace_dict[a%d]=c%d"%(i,i))
    exec("replace_dict[alpha%d]=epsilon%d*c%d"%(i,i,i))
    exec("replace_dict_equal[epsilon%d]=epsilon"%(i))
    exec("replace_dict_equal[c%d]=c"%(i))
    exec("replace_dict_equal[kb%d]=kb"%(i))
    exec("replace_dict_equal[ku%d]=ku"%(i))
print(edges)

[[1, 'a1', 2], [6, 'alpha1', 7], [1, 'kb1-x', 6], [6, 'ku1', 1], [2, 'a2', 3], [7, 'alpha2', 8], [2, 'kb2-x', 7], [7, 'ku2', 2], [3, 'a3', 4], [8, 'alpha3', 9], [3, 'kb3-x', 8], [8, 'ku3', 3], [4, 'a4', 5], [9, 'alpha4', 10], [4, 'kb4-x', 9], [9, 'ku4', 4], [5, 'a5', 1], [10, 'alpha5', 6], [5, 'kb5-x', 10], [10, 'ku5', 5]]


In [3]:
replace_dict

{a1: c1,
 alpha1: c1*epsilon1,
 a2: c2,
 alpha2: c2*epsilon2,
 a3: c3,
 alpha3: c3*epsilon3,
 a4: c4,
 alpha4: c4*epsilon4,
 a5: c5,
 alpha5: c5*epsilon5}

In [4]:

MTTfolder='../../shared/utilsGRF' #folder with MTT.py 
basename='graph'

parlist=[x[1] for x in edges]
parlist=list(set(parlist))


for pnum,par in enumerate(parlist):
    if '-x' in par:
        parlist[pnum]=parlist[pnum].replace('-x','')
print(parlist)

graphname=os.path.join(MTTfolder,basename+'.txt')
outf=open(graphname,'w')
for x in edges:
    x_str=list(map(str,x))
    outf.write('('+','.join(x_str)+') ')
outf.close()

#execute_MTT(self):

args=["python",os.path.join(MTTfolder,'MTT.py'),graphname]
print("executing MTT")
print(subprocess.check_call(args))


#parse_rhos_from_graphfiles(self):
#this was previously called rhos_from_edges
edges=np.array(edges)
#find files that correspond to the spanning trees
files=glob.glob(os.path.join(MTTfolder,basename+'*'))
pat=re.compile('[0-9]+.txt')
n=0
for f in files:
    if pat.findall(f):
        n+=1
all_rhos=[] 
allGraphs=dict()
allterms=dict()
for i in range(1,n+1):
    fname=os.path.join(MTTfolder,basename+'-%d.txt'%i)

    fi=open(fname,'r')
    rho_expr='rho_%d='%i
    allGraphs[i]=[]
    allterms[i]=[]
    for lnum,l in enumerate(fi.readlines()):
        idxs=np.array(list(map(int,l.strip().split())),dtype=bool)
        subset=edges[idxs]
        expr=[x[1] for x in subset] #labels that multiply together in a term of the rho
        term='*'.join(expr)
        if lnum<1:
            rho_expr=rho_expr+term
        else:
            rho_expr=rho_expr+'+'+term
        allterms[i].append(term)
        #now get Graph
        G=nx.DiGraph()
        for edge in subset:
            n0=int(edge[0])
            n1=int(edge[2])
            par=edge[1]
            G.add_edge(n0,n1,name=par)
            G.add_edge
        allGraphs[i].append(G)
        
            
        

    all_rhos.append(rho_expr)

['alpha5', 'kb1', 'a1', 'alpha1', 'ku5', 'a5', 'ku1', 'a3', 'ku4', 'kb5', 'alpha2', 'a4', 'ku2', 'kb3', 'ku3', 'alpha4', 'alpha3', 'kb4', 'a2', 'kb2']
executing MTT
0


In [5]:
import re
kbpat=re.compile("kb")
alphapat=re.compile("alpha[0-9]")
#alpharepat=re.compile("alpha[0-9]r")
apat=re.compile("^a[0-9]|\*a[0-9]")
kupat=re.compile("ku[0-9]")

#Get mapping between trees rooted at bound state and trees rooted at unbound state:
- if there is a binding edge to the root: change for the unbinding edge and that's it
- if there is not a binding edge to the root: same number of alphas and as but at different places?


In [6]:
#the root+term number is an id for the trees

In [7]:
nnodes=nnodes_cycle
trees_nb=allterms[2*nnodes]
Gs_nb=allGraphs[2*nnodes]
trees_nu=allterms[nnodes]
Gs_nu=allGraphs[nnodes]
dx=5
dy=0.2
#coords={1:(2,0.8),2:(3,0.6),3:(4,0.4),4:(3,0.2),5:(2,0.2),6:(1,0.4),7:(0,0.6),8:(1,0.8),
#        9:(2+dx,0.8+dy),10:(3+dx,0.6+dy),11:(4+dx,0.4+dy),12:(3+dx,0.2+dy),13:(2+dx,0.2+dy),14:(1+dx,0.4+dy),
#        15:(0+dx,0.6+dy),16:(1+dx,0.8+dy)}
coords={1:(2,0.8),2:(3,0.6),3:(4,0.4),4:(2.5,0.2),5:(1.5,0.2),6:(0.5,0.4),7:(1,0.6),8:(1.5,0.7)}
coords2=coords.copy()
for key in coords.keys():
    k0,k1=coords[key]
    coords2[key+nnodes]=(k0+dx,k1+dy)

In [11]:
#relationship between a_j,b and a_j-1,u
for n in range(1,nnodes+1): #for trees with n kb edges
    
    #Gs_b_kb=[] #trees with kb directly to root node
    #Gs_b_nokb=[] #trees with no kb directly to root node
    Gs_b=[]
    terms_b=[]
    terms_b_s=[]
    for t,term in enumerate(trees_nb):
        kbs=kbpat.findall(term)
        if len(kbs)==n:
            term_s=parse_expr(term.replace("-x",""))
            term_s=term_s.subs(replace_dict)
            term_s=term_s.subs(replace_dict_equal)
            G=Gs_nb[t]
            Gs_b.append(G)
            na=len(apat.findall(term))
            nalpha=len(alphapat.findall(term))
            nku=len(kupat.findall(term))
            terms_b.append(np.array([na,nku,nalpha],dtype=int))
            terms_b_s.append(term_s)
            #print("a:%d,alpha:%d,ku:%d"%(na,nalpha,nku),term)
    
    
    Gs_u=[]
    terms_u=[]
    terms_u_s=[]
    for t,term in enumerate(trees_nu):
        kbs=kbpat.findall(term)
        if len(kbs)==(n-1):
            term_s=parse_expr(term.replace("-x",""))
            term_s=term_s.subs(replace_dict)
            term_s=term_s.subs(replace_dict_equal)
            #display(term_s)
            G=Gs_nu[t]
            Gs_u.append(G)
            na=len(apat.findall(term))
            nalpha=len(alphapat.findall(term))
            nku=len(kupat.findall(term))
            #print("a:%d,alpha:%d,ku:%d"%(na,nalpha,nku),term)
            terms_u.append(",".join(map(str,[na,nku,nalpha])))
            terms_u_s.append(term_s)
    
    
    if len(terms_b)>1:
        terms_b_,idxs,counts=np.unique(np.vstack(terms_b),axis=0,return_index=True,return_counts=True)
    elif len(terms_b)==1:
        terms_b_=terms_b
        counts=[1]
        idxs=[0]
    else:
        print("no trees in b!!")
    print(n,len(terms_b_))
    
    correspondance=[]
    print(idxs)
    print(counts)
    for i in range(len(idxs)):
        term_s=terms_b_s[idxs[i]]
        reverse=term_s*ku/kb
        countu=0
        for iu in range(len(terms_u_s)):
            if terms_u_s[iu]-reverse==0:
                correspondance.append(iu)
                countu+=1
        print(".",countu==counts[i])
            
    for i in range(len(terms_u)):
        if not i in correspondance:
            print("tree %d missing"%i, terms_u[i])

    
    
            
                
                        

1 5
[4 2 3 1 0]
[ 5 10 10  5  1]
. True
. True
. True
. True
. True
2 4
[7 2 1 0]
[10 20 15  4]
. True
. True
. True
. True
3 3
[5 1 0]
[10 15  6]
. True
. True
. True
4 2
[1 0]
[5 4]
. True
. True
5 1
[0]
[1]
. True


In [16]:
term_s.subs()

a1*a2*a3*a4*kb5*ku1*ku2*ku3*ku4

In [25]:
import math

def nchoosek(n,k):
    #print("n",n,"k",k)
    return math.factorial(n)/(math.factorial(n-k)*math.factorial(k))

def c_formula(n,m,r):
    try:
        num=n*nchoosek(n-1,m)*nchoosek(m,r)
    except ValueError as e:
        print(n-1,"choose",m,";",m,"choose",r)
        raise e
    den=n-m+r
    return num/den

In [17]:
## relationship between a_j,b and a_j-1,b
Y=[]
for t,term in enumerate(trees_nb):
    kbs=kbpat.findall(term)
    if len(kbs)==nnodes:
        term_s=parse_expr(term.replace("-x",""))
        term_s=term_s.subs(replace_dict)
        term_s=term_s.subs(replace_dict_equal)
        Y.append(term_s)
        #print("a:%d,alpha:%d,ku:%d"%(na,nalpha,nku),term)

if len(Y)!=1:
    print("wrong Y!!!")
else:
    Y=Y[0]
    
for k in range(1,nnodes): #for trees with k kb edges, i.e. degree k, so m=nnodes-k modifications
    
    #Gs_b_kb=[] #trees with kb directly to root node
    #Gs_b_nokb=[] #trees with no kb directly to root node
    Gs_b=[]
    terms_b_s=[]
    for t,term in enumerate(trees_nb):
        kbs=kbpat.findall(term)
        if len(kbs)==k:
            term_s=parse_expr(term.replace("-x",""))
            term_s=term_s.subs(replace_dict)
            term_s=term_s.subs(replace_dict_equal)
            terms_b.append(np.array([na,nku,nalpha],dtype=int))
            terms_b_s.append(term_s)
        
       
    #now show that I can get each of the trees by applying deletions and reversions from the original tree Y
    m=nnodes-k
    correspondance=np.zeros(len(terms_b_s))
    for r in range(0,m+1):
        combinations=c_formula(nnodes,m,r)
        tree=Y*(c**(m-r)/kb**m)*(ku/epsilon)**r
        count=0
        for t,term in enumerate(terms_b_s):
            if term-tree==0:
                count+=1
                correspondance[t]=1
        print(count==combinations)
    if np.any(correspondance==0):
        print("Not all trees found!")
    elif np.sum(correspondance)==len(correspondance):
        print("*")
    
    
            
                
                        

True
True
True
True
True
*
True
True
True
True
*
True
True
True
*
True
True
*


In [ ]:
c_formula(5,)

In [39]:
#Now show that the condition for the derivative is true
for n in np.arange(5,25):
    for i in np.arange(1,n-1): #if i=0, theta_bi=0 and so there is no negative right hand side and the result is surely positive
        for j in np.arange(i+1,n):#if j==n, theta_uj=0 and so there is no negative right hand side either
            g=j-i
            m2=n-i-g
            m2_=m2-1
            m1_=n-i
            m1=m1_-1
            print("n:",n,", i:",i,", j:",j,",m1:",m1,",m2:",m2,",m1_:",m1_,"m2_:",m2_)
            if m1+m2!=m1_+m2_:
                print("Unequal sums")
                raise ValueError
            #sums <k2
            for S in np.arange(0,m1+m2+1):
                print(S)
                left=0
                right=0
                minr1=max(S-m2,0)
                maxr1=min(S,m1)
                for r1 in range(minr1,maxr1+1):
                    r2=S-r1
                    print("    :",r1,r2)
                    if r2<0:
                        print("negative r2")
                    if r2>m2:
                        print("r2 is too high")
                        raise ValueError
                    f1=c_formula(n,m1,r1)
                    f2=c_formula(n,m2,r2)
                    f12=f1*f2
                    left+=f12
                
                minr1_=max(S-m2_,0)
                maxr1_=min(S,m1_)
                for r1_ in range(minr1_,maxr1_+1):

                    r2_=S-r1_
                    print("    _:",r1_,r2_)
                    
                    if r2_<0:
                        print("negative r2_", S,r1_,r2_)
                    if r2_>m2_:
                        print("r2_ is too high")
                        raise ValueError
                    #print("    bar:", r1_,k1_,r2_,k2_,r1_+r2_,)

                    f1_=c_formula(n,m1_,r1_)
                    f2_=c_formula(n,m2_,r2_)
                    f12_=f1_*f2_
                    right+=f12_
                    #if f12<f12_:
                    #    print("S:%d, r1:%d, r2:%d, k1:%d, k2: %d, k1_:%d, k2_:%d, f12:%d, f12_:%d"%(S,r1,r2,k1,k2,k1_,k2_,f12,f12_))
                if left-right<0:

                    print("**not fulfilled for n=%d, i=%d, g=%d, S=%d"%(n, i,g,S))
            print(" ")
    

n: 5 , i: 1 , j: 2 ,m1: 3 ,m2: 3 ,m1_: 4 m2_: 2
0
    : 0 0
    _: 0 0
1
    : 0 1
    : 1 0
    _: 0 1
    _: 1 0
2
    : 0 2
    : 1 1
    : 2 0
    _: 0 2
    _: 1 1
    _: 2 0
3
    : 0 3
    : 1 2
    : 2 1
    : 3 0
    _: 1 2
    _: 2 1
    _: 3 0
4
    : 1 3
    : 2 2
    : 3 1
    _: 2 2
    _: 3 1
    _: 4 0
5
    : 2 3
    : 3 2
    _: 3 2
    _: 4 1
6
    : 3 3
    _: 4 2
 
n: 5 , i: 1 , j: 3 ,m1: 3 ,m2: 2 ,m1_: 4 m2_: 1
0
    : 0 0
    _: 0 0
1
    : 0 1
    : 1 0
    _: 0 1
    _: 1 0
2
    : 0 2
    : 1 1
    : 2 0
    _: 1 1
    _: 2 0
3
    : 1 2
    : 2 1
    : 3 0
    _: 2 1
    _: 3 0
4
    : 2 2
    : 3 1
    _: 3 1
    _: 4 0
5
    : 3 2
    _: 4 1
 
n: 5 , i: 1 , j: 4 ,m1: 3 ,m2: 1 ,m1_: 4 m2_: 0
0
    : 0 0
    _: 0 0
1
    : 0 1
    : 1 0
    _: 1 0
2
    : 1 1
    : 2 0
    _: 2 0
3
    : 2 1
    : 3 0
    _: 3 0
4
    : 3 1
    _: 4 0
 
n: 5 , i: 2 , j: 3 ,m1: 2 ,m2: 2 ,m1_: 3 m2_: 1
0
    : 0 0
    _: 0 0
1
    : 0 1
    : 1 0
    _: 0 1
    _: 1 0
2
    : 0

    _: 1 3
    _: 2 2
    _: 3 1
    _: 4 0
5
    : 0 5
    : 1 4
    : 2 3
    : 3 2
    : 4 1
    : 5 0
    _: 1 4
    _: 2 3
    _: 3 2
    _: 4 1
    _: 5 0
6
    : 1 5
    : 2 4
    : 3 3
    : 4 2
    : 5 1
    : 6 0
    _: 2 4
    _: 3 3
    _: 4 2
    _: 5 1
    _: 6 0
7
    : 2 5
    : 3 4
    : 4 3
    : 5 2
    : 6 1
    _: 3 4
    _: 4 3
    _: 5 2
    _: 6 1
    _: 7 0
8
    : 3 5
    : 4 4
    : 5 3
    : 6 2
    _: 4 4
    _: 5 3
    _: 6 2
    _: 7 1
9
    : 4 5
    : 5 4
    : 6 3
    _: 5 4
    _: 6 3
    _: 7 2
10
    : 5 5
    : 6 4
    _: 6 4
    _: 7 3
11
    : 6 5
    _: 7 4
 
n: 8 , i: 1 , j: 4 ,m1: 6 ,m2: 4 ,m1_: 7 m2_: 3
0
    : 0 0
    _: 0 0
1
    : 0 1
    : 1 0
    _: 0 1
    _: 1 0
2
    : 0 2
    : 1 1
    : 2 0
    _: 0 2
    _: 1 1
    _: 2 0
3
    : 0 3
    : 1 2
    : 2 1
    : 3 0
    _: 0 3
    _: 1 2
    _: 2 1
    _: 3 0
4
    : 0 4
    : 1 3
    : 2 2
    : 3 1
    : 4 0
    _: 1 3
    _: 2 2
    _: 3 1
    _: 4 0
5
    : 1 4
    : 2 3
    : 3 2

    _: 6 1
    _: 7 0
8
    : 3 5
    : 4 4
    : 5 3
    : 6 2
    : 7 1
    _: 4 4
    _: 5 3
    _: 6 2
    _: 7 1
    _: 8 0
9
    : 4 5
    : 5 4
    : 6 3
    : 7 2
    _: 5 4
    _: 6 3
    _: 7 2
    _: 8 1
10
    : 5 5
    : 6 4
    : 7 3
    _: 6 4
    _: 7 3
    _: 8 2
11
    : 6 5
    : 7 4
    _: 7 4
    _: 8 3
12
    : 7 5
    _: 8 4
 
n: 9 , i: 1 , j: 5 ,m1: 7 ,m2: 4 ,m1_: 8 m2_: 3
0
    : 0 0
    _: 0 0
1
    : 0 1
    : 1 0
    _: 0 1
    _: 1 0
2
    : 0 2
    : 1 1
    : 2 0
    _: 0 2
    _: 1 1
    _: 2 0
3
    : 0 3
    : 1 2
    : 2 1
    : 3 0
    _: 0 3
    _: 1 2
    _: 2 1
    _: 3 0
4
    : 0 4
    : 1 3
    : 2 2
    : 3 1
    : 4 0
    _: 1 3
    _: 2 2
    _: 3 1
    _: 4 0
5
    : 1 4
    : 2 3
    : 3 2
    : 4 1
    : 5 0
    _: 2 3
    _: 3 2
    _: 4 1
    _: 5 0
6
    : 2 4
    : 3 3
    : 4 2
    : 5 1
    : 6 0
    _: 3 3
    _: 4 2
    _: 5 1
    _: 6 0
7
    : 3 4
    : 4 3
    : 5 2
    : 6 1
    : 7 0
    _: 4 3
    _: 5 2
    _: 6 1
    _: 7 

    : 3 3
    _: 4 2
 
n: 9 , i: 5 , j: 7 ,m1: 3 ,m2: 2 ,m1_: 4 m2_: 1
0
    : 0 0
    _: 0 0
1
    : 0 1
    : 1 0
    _: 0 1
    _: 1 0
2
    : 0 2
    : 1 1
    : 2 0
    _: 1 1
    _: 2 0
3
    : 1 2
    : 2 1
    : 3 0
    _: 2 1
    _: 3 0
4
    : 2 2
    : 3 1
    _: 3 1
    _: 4 0
5
    : 3 2
    _: 4 1
 
n: 9 , i: 5 , j: 8 ,m1: 3 ,m2: 1 ,m1_: 4 m2_: 0
0
    : 0 0
    _: 0 0
1
    : 0 1
    : 1 0
    _: 1 0
2
    : 1 1
    : 2 0
    _: 2 0
3
    : 2 1
    : 3 0
    _: 3 0
4
    : 3 1
    _: 4 0
 
n: 9 , i: 6 , j: 7 ,m1: 2 ,m2: 2 ,m1_: 3 m2_: 1
0
    : 0 0
    _: 0 0
1
    : 0 1
    : 1 0
    _: 0 1
    _: 1 0
2
    : 0 2
    : 1 1
    : 2 0
    _: 1 1
    _: 2 0
3
    : 1 2
    : 2 1
    _: 2 1
    _: 3 0
4
    : 2 2
    _: 3 1
 
n: 9 , i: 6 , j: 8 ,m1: 2 ,m2: 1 ,m1_: 3 m2_: 0
0
    : 0 0
    _: 0 0
1
    : 0 1
    : 1 0
    _: 1 0
2
    : 1 1
    : 2 0
    _: 2 0
3
    : 2 1
    _: 3 0
 
n: 9 , i: 7 , j: 8 ,m1: 1 ,m2: 1 ,m1_: 2 m2_: 0
0
    : 0 0
    _: 0 0
1
    : 0 1
    : 1

    : 3 5
    : 4 4
    : 5 3
    : 6 2
    : 7 1
    _: 3 5
    _: 4 4
    _: 5 3
    _: 6 2
    _: 7 1
    _: 8 0
9
    : 3 6
    : 4 5
    : 5 4
    : 6 3
    : 7 2
    _: 4 5
    _: 5 4
    _: 6 3
    _: 7 2
    _: 8 1
10
    : 4 6
    : 5 5
    : 6 4
    : 7 3
    _: 5 5
    _: 6 4
    _: 7 3
    _: 8 2
11
    : 5 6
    : 6 5
    : 7 4
    _: 6 5
    _: 7 4
    _: 8 3
12
    : 6 6
    : 7 5
    _: 7 5
    _: 8 4
13
    : 7 6
    _: 8 5
 
n: 10 , i: 2 , j: 5 ,m1: 7 ,m2: 5 ,m1_: 8 m2_: 4
0
    : 0 0
    _: 0 0
1
    : 0 1
    : 1 0
    _: 0 1
    _: 1 0
2
    : 0 2
    : 1 1
    : 2 0
    _: 0 2
    _: 1 1
    _: 2 0
3
    : 0 3
    : 1 2
    : 2 1
    : 3 0
    _: 0 3
    _: 1 2
    _: 2 1
    _: 3 0
4
    : 0 4
    : 1 3
    : 2 2
    : 3 1
    : 4 0
    _: 0 4
    _: 1 3
    _: 2 2
    _: 3 1
    _: 4 0
5
    : 0 5
    : 1 4
    : 2 3
    : 3 2
    : 4 1
    : 5 0
    _: 1 4
    _: 2 3
    _: 3 2
    _: 4 1
    _: 5 0
6
    : 1 5
    : 2 4
    : 3 3
    : 4 2
    : 5 1
    : 6 0


...

    _: 0 1
    _: 1 0
2
    : 0 2
    : 1 1
    : 2 0
    _: 0 2
    _: 1 1
    _: 2 0
3
    : 0 3
    : 1 2
    : 2 1
    : 3 0
    _: 0 3
    _: 1 2
    _: 2 1
    _: 3 0
4
    : 0 4
    : 1 3
    : 2 2
    : 3 1
    : 4 0
    _: 0 4
    _: 1 3
    _: 2 2
    _: 3 1
    _: 4 0
5
    : 0 5
    : 1 4
    : 2 3
    : 3 2
    : 4 1
    : 5 0
    _: 1 4
    _: 2 3
    _: 3 2
    _: 4 1
    _: 5 0
6
    : 1 5
    : 2 4
    : 3 3
    : 4 2
    : 5 1
    : 6 0
    _: 2 4
    _: 3 3
    _: 4 2
    _: 5 1
    _: 6 0
7
    : 2 5
    : 3 4
    : 4 3
    : 5 2
    : 6 1
    : 7 0
    _: 3 4
    _: 4 3
    _: 5 2
    _: 6 1
    _: 7 0
8
    : 3 5
    : 4 4
    : 5 3
    : 6 2
    : 7 1
    : 8 0
    _: 4 4
    _: 5 3
    _: 6 2
    _: 7 1
    _: 8 0
9
    : 4 5
    : 5 4
    : 6 3
    : 7 2
    : 8 1
    : 9 0
    _: 5 4
    _: 6 3
    _: 7 2
    _: 8 1
    _: 9 0
10
    : 5 5
    : 6 4
    : 7 3
    : 8 2
    : 9 1
    : 10 0
    _: 6 4
    _: 7 3
    _: 8 2
    _: 9 1
    _: 10 0
11
    : 6 5
  

    : 10 7
    _: 10 7
    _: 11 6
18
    : 10 8
    _: 11 7
 
n: 24 , i: 13 , j: 17 ,m1: 10 ,m2: 7 ,m1_: 11 m2_: 6
0
    : 0 0
    _: 0 0
1
    : 0 1
    : 1 0
    _: 0 1
    _: 1 0
2
    : 0 2
    : 1 1
    : 2 0
    _: 0 2
    _: 1 1
    _: 2 0
3
    : 0 3
    : 1 2
    : 2 1
    : 3 0
    _: 0 3
    _: 1 2
    _: 2 1
    _: 3 0
4
    : 0 4
    : 1 3
    : 2 2
    : 3 1
    : 4 0
    _: 0 4
    _: 1 3
    _: 2 2
    _: 3 1
    _: 4 0
5
    : 0 5
    : 1 4
    : 2 3
    : 3 2
    : 4 1
    : 5 0
    _: 0 5
    _: 1 4
    _: 2 3
    _: 3 2
    _: 4 1
    _: 5 0
6
    : 0 6
    : 1 5
    : 2 4
    : 3 3
    : 4 2
    : 5 1
    : 6 0
    _: 0 6
    _: 1 5
    _: 2 4
    _: 3 3
    _: 4 2
    _: 5 1
    _: 6 0
7
    : 0 7
    : 1 6
    : 2 5
    : 3 4
    : 4 3
    : 5 2
    : 6 1
    : 7 0
    _: 1 6
    _: 2 5
    _: 3 4
    _: 4 3
    _: 5 2
    _: 6 1
    _: 7 0
8
    : 1 7
    : 2 6
    : 3 5
    : 4 4
    : 5 3
    : 6 2
    : 7 1
    : 8 0
    _: 2 6
    _: 3 5
    _: 4 4
    _: 5

    _: 3 7
    _: 4 6
    _: 5 5
    _: 6 4
    _: 7 3
    _: 8 2
    _: 9 1
    _: 10 0
11
    : 3 8
    : 4 7
    : 5 6
    : 6 5
    : 7 4
    : 8 3
    : 9 2
    _: 4 7
    _: 5 6
    _: 6 5
    _: 7 4
    _: 8 3
    _: 9 2
    _: 10 1
12
    : 4 8
    : 5 7
    : 6 6
    : 7 5
    : 8 4
    : 9 3
    _: 5 7
    _: 6 6
    _: 7 5
    _: 8 4
    _: 9 3
    _: 10 2
13
    : 5 8
    : 6 7
    : 7 6
    : 8 5
    : 9 4
    _: 6 7
    _: 7 6
    _: 8 5
    _: 9 4
    _: 10 3
14
    : 6 8
    : 7 7
    : 8 6
    : 9 5
    _: 7 7
    _: 8 6
    _: 9 5
    _: 10 4
15
    : 7 8
    : 8 7
    : 9 6
    _: 8 7
    _: 9 6
    _: 10 5
16
    : 8 8
    : 9 7
    _: 9 7
    _: 10 6
17
    : 9 8
    _: 10 7
 
n: 24 , i: 14 , j: 17 ,m1: 9 ,m2: 7 ,m1_: 10 m2_: 6
0
    : 0 0
    _: 0 0
1
    : 0 1
    : 1 0
    _: 0 1
    _: 1 0
2
    : 0 2
    : 1 1
    : 2 0
    _: 0 2
    _: 1 1
    _: 2 0
3
    : 0 3
    : 1 2
    : 2 1
    : 3 0
    _: 0 3
    _: 1 2
    _: 2 1
    _: 3 0
4
    : 0 4
    : 1 3
 

    : 7 6
    : 8 5
    _: 7 6
    _: 8 5
    _: 9 4
14
    : 7 7
    : 8 6
    _: 8 6
    _: 9 5
15
    : 8 7
    _: 9 6
 
n: 24 , i: 15 , j: 18 ,m1: 8 ,m2: 6 ,m1_: 9 m2_: 5
0
    : 0 0
    _: 0 0
1
    : 0 1
    : 1 0
    _: 0 1
    _: 1 0
2
    : 0 2
    : 1 1
    : 2 0
    _: 0 2
    _: 1 1
    _: 2 0
3
    : 0 3
    : 1 2
    : 2 1
    : 3 0
    _: 0 3
    _: 1 2
    _: 2 1
    _: 3 0
4
    : 0 4
    : 1 3
    : 2 2
    : 3 1
    : 4 0
    _: 0 4
    _: 1 3
    _: 2 2
    _: 3 1
    _: 4 0
5
    : 0 5
    : 1 4
    : 2 3
    : 3 2
    : 4 1
    : 5 0
    _: 0 5
    _: 1 4
    _: 2 3
    _: 3 2
    _: 4 1
    _: 5 0
6
    : 0 6
    : 1 5
    : 2 4
    : 3 3
    : 4 2
    : 5 1
    : 6 0
    _: 1 5
    _: 2 4
    _: 3 3
    _: 4 2
    _: 5 1
    _: 6 0
7
    : 1 6
    : 2 5
    : 3 4
    : 4 3
    : 5 2
    : 6 1
    : 7 0
    _: 2 5
    _: 3 4
    _: 4 3
    _: 5 2
    _: 6 1
    _: 7 0
8
    : 2 6
    : 3 5
    : 4 4
    : 5 3
    : 6 2
    : 7 1
    : 8 0
    _: 3 5
    _: 4 4
  

    : 5 1
    : 6 0
    _: 6 0
7
    : 6 1
    : 7 0
    _: 7 0
8
    : 7 1
    _: 8 0
 
n: 24 , i: 17 , j: 18 ,m1: 6 ,m2: 6 ,m1_: 7 m2_: 5
0
    : 0 0
    _: 0 0
1
    : 0 1
    : 1 0
    _: 0 1
    _: 1 0
2
    : 0 2
    : 1 1
    : 2 0
    _: 0 2
    _: 1 1
    _: 2 0
3
    : 0 3
    : 1 2
    : 2 1
    : 3 0
    _: 0 3
    _: 1 2
    _: 2 1
    _: 3 0
4
    : 0 4
    : 1 3
    : 2 2
    : 3 1
    : 4 0
    _: 0 4
    _: 1 3
    _: 2 2
    _: 3 1
    _: 4 0
5
    : 0 5
    : 1 4
    : 2 3
    : 3 2
    : 4 1
    : 5 0
    _: 0 5
    _: 1 4
    _: 2 3
    _: 3 2
    _: 4 1
    _: 5 0
6
    : 0 6
    : 1 5
    : 2 4
    : 3 3
    : 4 2
    : 5 1
    : 6 0
    _: 1 5
    _: 2 4
    _: 3 3
    _: 4 2
    _: 5 1
    _: 6 0
7
    : 1 6
    : 2 5
    : 3 4
    : 4 3
    : 5 2
    : 6 1
    _: 2 5
    _: 3 4
    _: 4 3
    _: 5 2
    _: 6 1
    _: 7 0
8
    : 2 6
    : 3 5
    : 4 4
    : 5 3
    : 6 2
    _: 3 5
    _: 4 4
    _: 5 3
    _: 6 2
    _: 7 1
9
    : 3 6
    : 4 5
    : 5 4
  

In [30]:
import sympy

In [66]:
n,i,j,r_i,r_j,r_iu,r_ju,s,x,y=sympy.symbols("n,i,j,r_i,r_j,r_iu,r_ju,s,x,y")

In [69]:
def nchoosek_sympy(m,k):
    return sympy.factorial(m)/(sympy.factorial(k)*sympy.factorial(m-k))
def c_formula_sympy(n,degree,nr):
    f1=nchoosek_sympy(n-1,n-degree)
    f2=nchoosek_sympy(n-degree,nr)
    num=n*f1*f2
    den=degree+nr
    return num/den 

In [74]:
c_formula_sympy(n,i+1,r_iu)*c_formula_sympy(n,j,r_j)

n**2*factorial(n - 1)**2/((j + r_j)*(i + r_iu + 1)*factorial(i)*factorial(r_iu)*factorial(r_j)*factorial(j - 1)*factorial(-j + n - r_j)*factorial(-i + n - r_iu - 1))

In [77]:
def get_product(n,degree1,r1,degree2,r2):
    return sympy.simplify(sympy.expand(c_formula_sympy(n,degree1,r1)*c_formula_sympy(n,degree2,r2)))


In [79]:
S=5
degree_iu=3
degree_j=5
nval=8
sums=[]
for riu in range(0,nval-degree_iu):
    for rj in range(0,nval-degree_j):
        if riu+rj==S:
            print(riu,rj)
            product=get_product(nval,degree_iu,riu,degree_j,rj)
            sums.append(product)
            

3 2
4 1


In [80]:
sums

[33600, 16800]

# Now taking into account that alphas and kus may not be all equal:
# this should be updated  

In [9]:
import sympy
from sympy.parsing.sympy_parser import parse_expr 

In [10]:
a1,a2,a3,a4,a5,a6,a7,a8=sympy.symbols("a1,a2,a3,a4,a5,a6,a7,a8")
alpha1,alpha2,alpha3,alpha4,alpha5,alpha6,alpha7,alpha8=sympy.symbols("alpha1,alpha2,alpha3,alpha4,alpha5,alpha6,alpha7,alpha8")
ku1,ku2,ku3,ku4,ku5,ku6,ku7,ku8=sympy.symbols("ku1,ku2,ku3,ku4,ku5,ku6,ku7,ku8")
kb1,kb2,kb3,kb4,kb5,kb6,kb7,kb8=sympy.symbols("kb1,kb2,kb3,kb4,kb5,kb6,kb7,kb8")

cs=[a1,a2,a3,a4,a5,a6,a7,a8]
epsilons=[alpha1,alpha2,alpha3,alpha4,alpha5,alpha6,alpha7,alpha8]
kus=[ku1,ku2,ku3,ku4,ku5,ku6,ku7,ku8]
kbs=[kb1,kb2,kb3,kb4,kb5,kb6,kb7,kb8]

In [11]:
import itertools

In [12]:
list(itertools.combinations(np.arange(8),3))

[(0, 1, 2),
 (0, 1, 3),
 (0, 1, 4),
 (0, 1, 5),
 (0, 1, 6),
 (0, 1, 7),
 (0, 2, 3),
 (0, 2, 4),
 (0, 2, 5),
 (0, 2, 6),
 (0, 2, 7),
 (0, 3, 4),
 (0, 3, 5),
 (0, 3, 6),
 (0, 3, 7),
 (0, 4, 5),
 (0, 4, 6),
 (0, 4, 7),
 (0, 5, 6),
 (0, 5, 7),
 (0, 6, 7),
 (1, 2, 3),
 (1, 2, 4),
 (1, 2, 5),
 (1, 2, 6),
 (1, 2, 7),
 (1, 3, 4),
 (1, 3, 5),
 (1, 3, 6),
 (1, 3, 7),
 (1, 4, 5),
 (1, 4, 6),
 (1, 4, 7),
 (1, 5, 6),
 (1, 5, 7),
 (1, 6, 7),
 (2, 3, 4),
 (2, 3, 5),
 (2, 3, 6),
 (2, 3, 7),
 (2, 4, 5),
 (2, 4, 6),
 (2, 4, 7),
 (2, 5, 6),
 (2, 5, 7),
 (2, 6, 7),
 (3, 4, 5),
 (3, 4, 6),
 (3, 4, 7),
 (3, 5, 6),
 (3, 5, 7),
 (3, 6, 7),
 (4, 5, 6),
 (4, 5, 7),
 (4, 6, 7),
 (5, 6, 7)]

In [83]:
Y=sympy.Mul(*kbs)*sympy.Mul(*epsilons)/epsilons[-1]
display(Y)
csar=np.array(cs)
epsilonsar=np.array(epsilons)
kusar=np.array(kus)
kbsar=np.array(kbs)
## relationship between a_j,b and a_j-1,b
for m in range(1,nnodes):#number of modifications
    degree=nnodes-m

    #Gs_b_kb=[] #trees with kb directly to root node
    #Gs_b_nokb=[] #trees with no kb directly to root node
    Gs_b=[]
    terms_jb=[]
    terms_jb_1_del=[]
    terms_jb_1_rev=[]

    
    #deletions only:
    combis=itertools.combinations(np.arange(nnodes),m)
    for combi in combis:
        if len(combi)>1:
            combi=list(combi)
            csterm=sympy.Mul(*csar[combi])
            kbsterm=sympy.Mul(*kbsar[combi])
        else:
            csterm=csar[combi[0]]
            kbsterm=kbsar[combi[0]]
            
            print(csterm)
        term2=Y*csterm/kbsterm
        terms_jb_1_del.append(term2)
        
    #reversions only
    combis=itertools.combinations(np.arange(nnodes-1),m)
    for combi in combis:
        if len(combi)>1:
            combi=list(combi)
            csterm=sympy.Mul(*csar[combi])
            kbsterm=sympy.Mul(*kbsar[combi])
            kusterm=sympy.Mul(*kusar[combi])
            epsterm=sympy.Mul(*epsilonsar[combi])
        else:
            csterm=csar[combi[0]]
            kbsterm=kbsar[combi[0]]
            kusterm=kusar[combi[0]]
            epsterm=epsilonsar[combi[0]]
        term2=Y*(csterm*kusterm)/(kbsterm*epsterm)
        terms_jb_1_rev.append(term2)
        
    #reversions and deletions (only possible if at least two edges modified)
    terms_jb_1_rev_del=[]
    rev_del_strings=[]
    
    if m>1:
        for nd in range(1,m):
            nr=m-nd
            print(m,"nr:%d,nd:%d"%(nr,nd))
        
            #first keep kb:
            combis=itertools.combinations(np.arange(nnodes-1),m) #combinations of edges affected
            for combi_ in combis:
                for combi in itertools.combinations(combi_,nr): #select edges reversed
                    #print("edges affected",combi_, "edges reversed", combi)
                    if len(combi)==1:
                        csterm=csar[combi[0]]
                        kbsterm=kbsar[combi[0]]
                        kusterm=kusar[combi[0]]
                        epsterm=epsilonsar[combi[0]]
                    else:
                        combi=list(combi)
                        csterm=sympy.Mul(*csar[combi])
                        kbsterm=sympy.Mul(*kbsar[combi])
                        kusterm=sympy.Mul(*kusar[combi])
                        epsterm=sympy.Mul(*epsilonsar[combi])
                    term2=Y*(csterm*kusterm)/(kbsterm*epsterm)
                    
                    #now add the edges deleted:
                    combidel=[]
                    for i in combi_:
                        if not i in combi:#if the edge was not reversed, add to the list of edges to delete
                            combidel.append(i)
                    if len(combidel)==0:
                        print("wrong!Cannot be. Exiting")
                        sys.exit()
                    elif len(combidel)==1:
                        csterm=csar[combidel[0]]
                        kbsterm=kbsar[combidel[0]]
                    else:
                        csterm=sympy.Mul(*csar[combidel])
                        kbsterm=sympy.Mul(*kbsar[combidel])
                        
                    term2=term2*csterm/kbsterm
                    
                    termstring=""
                    for i in sorted(combi):
                        termstring+="%dr,"%i
                    for i in sorted(combidel):
                        termstring+="%dd,"%i
                    if not termstring in rev_del_strings:
                        terms_jb_1_rev_del.append(term2)
                        rev_del_strings.append(term2)
                        
                        
            
            #now delete kb (cannot be reversed). So combinations of edges<n, and one modification less because one is the deletion of n
            combis=itertools.combinations(np.arange(nnodes-1),m-1) #combinations of edges affected
            for combi_ in combis:
                for combi in itertools.combinations(combi_,nr): #select edges reversed
                    maxirev=max(combi)
                    #now add the edges deleted:
                    combidel=[]
                    for i in combi_:
                        if not i in combi:
                            combidel.append(i)
                    cont=False
                    if len(combidel)==0:#means there was only 1 deletion and this was n
                        cont=True
                    else:
                        #need to check that at least one kb after the last reversion
                        allpresent=True
                        edges_after_lasterv=np.arange(maxirev+1,nnodes)
                        for i in edges_after_lasterv:
                            if not i in combidel:
                                allpresent=False
                        if not allpresent:
                            cont=True
                            
                    if cont:
                        cont2=False
                        termstring=""
                        for i in sorted(combi):
                            termstring+="%dr,"%i
                        for i in sorted(combidel):
                            termstring+="%dd,"%i
                        if not termstring in rev_del_strings:
                            cont2=True
                        if cont2:
                            if len(combi)==1:
                                csterm=csar[combi[0]]
                                kbsterm=kbsar[combi[0]]
                                kusterm=kusar[combi[0]]
                                epsterm=epsilonsar[combi[0]]
                            else:
                                combi=list(combi)
                                csterm=sympy.Mul(*csar[combi])
                                kbsterm=sympy.Mul(*kbsar[combi])
                                kusterm=sympy.Mul(*kusar[combi])
                                epsterm=sympy.Mul(*epsilonsar[combi])
                            term2=Y*(csar[-1]/kbsar[-1])*(csterm*kusterm)/(kbsterm*epsterm) #first csterm[-1]/kbsterm[-1] is the deletion of the last edge

                            
                            if len(combidel)==0:
                                terms_jb_1_rev_del.append(term2)
                                rev_del_strings.append(termstring)
                            else:
                                if len(combidel)==1:
                                    csterm=csar[combidel[0]]
                                    kbsterm=kbsar[combidel[0]]
                                elif len(combidel)>1:
                                    csterm=sympy.Mul(*csar[combidel])
                                    kbsterm=sympy.Mul(*kbsar[combidel])

                                term2=term2*csterm/kbsterm
                                terms_jb_1_rev_del.append(term2)
                                rev_del_strings.append(termstring)


    terms_jb_1_original=[]
    for t,term in enumerate(trees_nb):
        kbs_=kbpat.findall(term)
        if len(kbs_)==(degree):
            term_s=parse_expr(term.replace("-x",""))
            terms_jb_1_original.append(term_s)

    found=np.zeros(len(terms_jb_1_original),dtype=int)
    for t1,term1 in enumerate(terms_jb_1_original):#for each of the terms with one degree less, see where it is found    
        for t2,term2 in enumerate(terms_jb_1_del):
            #print(t1,t2)
            if term1-term2==0:
                found[t1]=1
                break
        if found[t1]==0:
            for t2,term2 in enumerate(terms_jb_1_rev):
                #print(t1,t2)
                if term1-term2==0:
                    found[t1]=2
                    break
        if found[t1]==0:
            for t2,term2 in enumerate(terms_jb_1_rev_del):
                #print(t1,t2)
                if term1-term2==0:
                    found[t1]=3
                    break
    print(m,"delete only",sum(found==1))
    print(m,"reverse only",sum(found==2))
    print(m,"reverse and delete",sum(found==3))
    print(m,"not found",sum(found==0),"*", sum(found==0)==0)
    notf=np.where(found==0)[0]
    #if len(notf)>0:
    #    for i in notf:
    #        display(terms_jb_1_original[i])
        
        
    
    
    
            
                
                        

alpha1*alpha2*alpha3*alpha4*alpha5*alpha6*alpha7*kb1*kb2*kb3*kb4*kb5*kb6*kb7*kb8

a1
a2
a3
a4
a5
a6
a7
a8
1 delete only 8
1 reverse only 7
1 reverse and delete 0
1 not found 0 * True
2 nr:1,nd:1
2 delete only 28
2 reverse only 21
2 reverse and delete 48
2 not found 0 * True
3 nr:2,nd:1
3 nr:1,nd:2
3 delete only 56
3 reverse only 35
3 reverse and delete 260
3 not found 0 * True
4 nr:3,nd:1
4 nr:2,nd:2
4 nr:1,nd:3
4 delete only 70
4 reverse only 35
4 reverse and delete 664
4 not found 0 * True
5 nr:4,nd:1
5 nr:3,nd:2
5 nr:2,nd:3
5 nr:1,nd:4
5 delete only 56
5 reverse only 21
5 reverse and delete 946
5 not found 0 * True
6 nr:5,nd:1
6 nr:4,nd:2
6 nr:3,nd:3
6 nr:2,nd:4
6 nr:1,nd:5
6 delete only 28
6 reverse only 7
6 reverse and delete 734
6 not found 0 * True
7 nr:6,nd:1
7 nr:5,nd:2
7 nr:4,nd:3
7 nr:3,nd:4
7 nr:2,nd:5
7 nr:1,nd:6
7 delete only 8
7 reverse only 1
7 reverse and delete 246
7 not found 0 * True


In [123]:
## relationship between a_j,b and a_j-1,u
Y=sympy.Mul(*kbs)*sympy.Mul(*epsilons)/epsilons[-1]
display(Y)
csar=np.array(cs)
epsilonsar=np.array(epsilons)
kusar=np.array(kus)
kbsar=np.array(kbs)

for m in range(1,nnodes+1):
    degree=nnodes-m
    print("degree", degree)
    
    terms_jb_1_original=[]
    terms_jb_1_original_string=[]
    for t,term in enumerate(trees_nb):
        kbs_=kbpat.findall(term)
        if len(kbs_)==(degree+1): #degree i in unbound from degree i+1 in bound
            term_s=parse_expr(term.replace("-x",""))
            terms_jb_1_original.append(term_s)
            terms_jb_1_original_string.append(term)
    terms_ju_2_original=[]
    for t,term in enumerate(trees_nu):
        kbs_=kbpat.findall(term)
        if len(kbs_)==(degree): #degree i in unbound from degree i+1 in bound
            term_s=parse_expr(term.replace("-x",""))
            terms_ju_2_original.append(term_s)

    terms_ju_2=[]
    for term in terms_jb_1_original:#see if I can get all terms in terms_ju_2_original from terms here
        #print("processing")
        #display(term)
        termsyms=term.free_symbols
        kus_present=[-1]
        kus_notpresent=[]
        kbs_present=[-1]
        for i in range(nnodes):
            kb_=kbs[i]
            if kb_ in termsyms:
                kbs_present.append(i)
        #print(kbs_present)
        for i in range(nnodes):
            ku_=kus[i]
            if ku_ in termsyms:
                kus_present.append(i)
            else:
                if i in kbs_present:
                    kus_notpresent.append(i) #I want the indices of the kus that are not present and can be reversed, so they have to be as kbs
        
        lastkb=max(kbs_present)
        lastku=max(kus_present) #if there are no kus, this will be -1, and so any kuidx will be greater
        for kuidx in kus_notpresent: 
            rev=False 
            if kuidx==lastkb: #there cannot be a remaining kb after the last reversion: so either reverse the last or one smaller
                rev=True
            elif kuidx < lastku:
                if lastku>lastkb: #no kb after the last ku, so this one can be reversed
                    rev=True
            elif kuidx>lastkb: #there cannot be a remaining kb after the last reversion
                rev=True
            if rev:
                if kuidx==(nnodes-1):#if it is kbn that is reversing, then only need to reverse
                    term2=term*(kus[kuidx]/kbs[kuidx])
                else:
                    reversion_effect=(kus[kuidx]/kbs[kuidx])*(cs[kuidx]/epsilons[kuidx])
                    term2=term*reversion_effect*(epsilons[-1]/cs[-1]) 
                    #since we are changing the root from n,b to nu, the last term adds epsilon_n and removes_cn 
                    #(kbn must have been deleted otherwise reversion of another edge with kbn present could not lead to a tree rooted at nu)
                
                terms_ju_2.append(term2)
    
    found=np.zeros(len(terms_ju_2_original),dtype=int)
    for t1,term1 in enumerate(terms_ju_2_original):#for each of the terms with one degree less, see where it is found    
        for t2,term2 in enumerate(terms_ju_2):
            #print(t1,t2)
            if term1-term2==0:
                found[t1]=1
                break
        
    print(m,"found",sum(found==1))
    print(m,"not found",sum(found==0),"*", sum(found==0)==0)
    notf=np.where(found==0)[0]
    if len(notf)>0:
        for i in notf:
            print("not found:")
            display(terms_ju_2_original[i])
                    

alpha1*alpha2*alpha3*alpha4*alpha5*alpha6*alpha7*kb1*kb2*kb3*kb4*kb5*kb6*kb7*kb8

degree 7
1 found 1
1 not found 0 * True
degree 6
2 found 15
2 not found 0 * True
degree 5
3 found 97
3 not found 0 * True
degree 4
4 found 351
4 not found 0 * True
degree 3
5 found 769
5 not found 0 * True
degree 2
6 found 1023
6 not found 0 * True
degree 1
7 found 769
7 not found 0 * True
degree 0
8 found 255
8 not found 0 * True


In [8]:
allterms.keys()

dict_keys([1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16])

In [13]:
i=2
j=4
b_i=[]
b_j=[]
for node in range(1,2*nnodes+1):
    for t,term in enumerate(allterms[node]):
            kbs=kbpat.findall(term)
            if len(kbs)==i:
                term_s=parse_expr(term.replace("-x",""))
                b_i.append(term_s)
            elif len(kbs)==j:
                term_s=parse_expr(term.replace("-x",""))
                b_j.append(term_s)
a_i=[]  
a_j=[]
for node in [nnodes,2*nnodes]:
    for t,term in enumerate(allterms[node]):
        kbs=kbpat.findall(term)
        if len(kbs)==i:
            term_s=parse_expr(term.replace("-x",""))
            if node>nnodes:
                a_i.append(epsilons[-1]*term_s)
            else:
                a_i.append(term_s)
        elif len(kbs)==j:
            term_s=parse_expr(term.replace("-x",""))
            if node>nnodes:
                a_i.append(epsilons[-1]*term_s)
            else:
                a_i.append(term_s)   


In [14]:
positive=[]
for term in b_i:
    for term2 in a_j:
        positive.append(term*term2)
negative=[]
for term in b_j:
    for term2 in a_i:
        negative.append(term*term2)
print(len(positive))
print(len(negative))

KeyboardInterrupt: 